## Import

In [1]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, TextStreamer

In [2]:
import pandas as pd
import numpy as np
import torch
from transformers import GPT2LMHeadModel, PreTrainedTokenizerFast, AdamW
from tqdm import tqdm



In [3]:
# CUDA 사용 가능 여부 확인
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Using device: cuda


In [4]:
class config():
    def __init__(self):
        
        self.source_len=128
        self.epochs = 10
        self.learning_rate=2e-5
        self.batch_size=16
        self.shuffle = True
        self.seed=800
        self.num_labels=10
        self.train_data_path= r'C:\Users\user\OneDrive - KookminUNIV\바탕 화면\DACON\train.csv'
        self.test_data_path = r'C:\Users\user\OneDrive - KookminUNIV\바탕 화면\DACON\test.csv'
        self.model_path = 'beomi/KoAlpaca-Polyglot-5.8B'
        # self.modelsave_path = r'C:\Users\user\OneDrive - KookminUNIV\바탕 화면\추가사전학습\Fine_tuning'
        # self.loss_path = r'C:\Users\user\OneDrive - KookminUNIV\바탕 화면\추가사전학습\Fine_tuning'
cfg = config()

## Data Preprocessing

In [7]:
data

id                          질문_1   
0    TRAIN_000                     면진장치가 뭐야?  \
1    TRAIN_001                내진설계의 종류 좀 알려줘   
2    TRAIN_002                 철골구조의 장점이 뭐야?   
3    TRAIN_003             철골철근 콘크리트 구조가 뭐야?   
4    TRAIN_004              철골구조는 어떤 방식이 있어?   
..         ...                           ...   
639  TRAIN_639             벽장 부위 결로의 원인이 뭐야?   
640  TRAIN_640     AD, PD에 면한 벽체 결로의 원인이 뭐야?   
641  TRAIN_641   외벽 모서리 부위에 결로가 발생하는 원인이 뭐야?   
642  TRAIN_642                창호 결로의 대책은 뭐야?   
643  TRAIN_643  AD, PD에 면한 벽체 결로에 대한 대책은 뭐야?   

                                      질문_2 category   
0                 면진장치에 사용되는 주요 기술은 무엇인가요?     건축구조  \
1        내진설계에는 어떤 종류가 있는지 자세히 알려주실 수 있나요?     건축구조   
2                           철골구조의 장점을 알려줘?     건축구조   
3         철골철근 콘크리트 구조의 장점과 단점에는 무엇이 있을까요?     건축구조   
4                     철골구조의 다양한 방식이 무엇인가요?     건축구조   
..                                     ...      ...   
639           벽장 부위 결로가 발생하는 주된 원인은 무엇일까요?   타 마감하자   
640       벽체 결로가 AD나 PD에 면한다면 그 원인이 무엇인가요?   타 마감하자   
641  외벽 모서리 부위에 결로가 발생하는 것을 예방하는 방법이 있을까요?   타 마감하자   
642      창호 결로를 해결하기 위한 가장 효과적인 방법은 무엇인가요?   타 마감하자   
643    AD, PD에 면한 벽체 결로에 대한 대책은 어떤 것이 있나요?   타 마감하자   

                                                  답변_1   
0    면진장치란 지반에서 오는 진동 에너지를 흡수하여 건물에 주는 진동을 줄여주는 진동 ...  \
1                   내진 설계의 종류로 내진구조, 제진구조, 면진구조가 있습니다.   
2    철골구조는 건물의 외벽에는 그다지 하중이 걸리지 않기 때문에 고층 건물의 건축이 가...   
3    철근철골콘크리트는 철골과 철근, 그리고 콘크리트를 함께 사용하는 건축 구조입니다. ...   
4                          철골구조는 일반철골구조와 경량철골구조가 있습니다.   
..                                                 ...   
639  벽장 부위 결로의 원인은 난방이 이웃한 방과동일한 조건이 되나 그 방에 비해 저온인...   
640  AD, PD에 면한 벽체 결로의 원인은 외기에 접하는 면 좌, 우측 벽체에는 단열재...   
641  외벽모서리 부위에 결로가 발생하는 원인은 높은 온도차 때문입니다. 외벽 모서리의 경...   
642  창호결로의 대책은 제품을 선정할 때 KS에 규정된 프레임을 선정하고 유리의 열관류율...   
643  AD, PD에 면한 벽체 결로에 대한 대책은 단열재를 미실하게 시공하여 결로가 생기...   

                                                  답변_2   
0    면진장치란 건물의 지반에서 발생하는 진동 에너지를 흡수하여 건물을 보호하고, 진동을...  \
1    내진설계에는 내진구조, 제진구조, 면진구조가 있습니다. 내진구조는 건물 구조물이 지...   
2    철골구조의 장점은 건물의 외벽에는 그다지 하중이 걸리지 않기 때문에 고층 건물의 건...   
3    철골철근콘크리트 구조는 건축물을 지탱하는 주요 구조물인 철골과 철근, 그리고 콘크리...   
4    철골구조는 일반철골구조와 경량철골구조가 있습니다. 일반철골구조는 주로 대형 건물이나...   
..                                                 ...   
639  벽장 부위 결로의 원인은 주로 난방이 자리잡은 방이 내부 온도가 낮은 반면, 외부 ...   
640  AD, PD에 면한 벽체 결로의 원인은 외기에 접하는 면 좌, 우측 벽체에는 단열재...   
641  외벽 모서리 부위에 결로가 발생하는 원인은 중요한 역할을 합니다. 외부에 비치는 세...   
642  창호 결로의 대책은 KS에 규정된 프레임을 선정하고 유리의 열관류율 및 결로 발생 ...   
643  AD, PD에 면한 벽체 결로에 대한 대책은 단열재를 미실하게 시공하여 결로가 생기...   

                                                  답변_3   
0    면진장치란 지반으로부터 발생하는 진동 에너지를 흡수하여 건물에 전달되는 진동을 줄여...  \
1    내진설계에는 주로 내진구조, 제진구조, 면진구조의 세 가지 종류가 있습니다. 이들은...   
2    철골구조의 장점은 건물의 외벽에 하중이 적게 걸리기 때문에 고층 건물의 건축이 용이...   
3    철골철근 콘크리트 구조는 건축물을 지탱하기 위한 구조물에서 일반적으로 사용되는 방식...   
4    철골구조는 주로 일반철골구조와 경량철골구조로 나뉘어집니다. 이들은 건축 시스템에 따...   
..                                                 ...   
639  벽장 부위 결로가 발생하는 원인은 난방이 잘 이루어지지 않아 해당 공간이 저온인 반...   
640  AD, PD에 면한 벽체 결로의 주된 원인은 외기에 접하는 면 좌, 우측 벽체에 단...   
641  외벽 모서리 부위에 결로가 발생하는 원인으로는 높은 온도차가 대표적입니다. 외벽 모...   
642  창호 결로를 예방하기 위한 대책은 KS에 규정된 프레임을 선택하고, 열관류율이 적은...   
643  AD, PD에 면한 벽체 결로에 대한 대책은 단열재를 미실하게 시공하여 결로가 생기...   

                                                  답변_4   
0    면진장치는 건물의 지반으로부터 오는 진동 에너지를 흡수하여 건물에 전달되는 진동을 ...  \
1    내진설계에는 주로 내진구조, 제진구조, 면진구조가 사용됩니다. 내진구조는 건물 구조...   
2    철골구조의 장점은 건물의 외벽이 하중이 걸리지 않아 공간 활용이 용이하고, 고층 건...   
3    철골철근콘크리트 구조는 철골과 철근, 그리고 콘크리트를 함께 사용하여 만들어지는 건...   
4    철골구조는 주로 일반철골구조와 경량철골구조로 구분됩니다. 이외에도 최근에는 고층 건...   
..                                                 ...   
639  벽장 부위 결로가 발생하는 원인은 난방이 인접한 방과 같은 조건을 갖추고 있지만, ...   
640  AD, PD에 면한 벽체 결로의 원인으로는 외기에 접하는 면 좌, 우측 벽체는 일반...   
641  외벽 모서리 부위에 결로가 발생하는 원인은 실내와 외부의 온도차 때문입니다. 외벽 ...   
642  창호 결로의 대책은 여러 가지가 있습니다. 먼저, 창호를 선택할 때 KS에 규정된 ...   
643  AD, PD에 면한 벽체 결로에 대한 대책은 단열재를 미실하게 시공하여 

In [18]:
tokenizer

PreTrainedTokenizerFast(name_or_path='beomi/polyglot-ko-12.8b-safetensors', vocab_size=30000, model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'eos_token': '<|endoftext|>', 'pad_token': '<|endoftext|>', 'additional_special_tokens': ['<|endoftext|>', '<|sep|>', '<|acc|>', '<|tel|>', '<|rrn|>']}, clean_up_tokenization_spaces=True)

In [17]:
# import torch
# from transformers import pipeline, AutoModelForCausalLM

# MODEL = 'beomi/KoAlpaca-Polyglot-5.8B'

# model = AutoModelForCausalLM.from_pretrained(
#     MODEL,
#     torch_dtype=torch.float16,
#     low_cpu_mem_usage=True,
# ).to(device=f"cuda", non_blocking=True)
# model.eval()

KeyboardInterrupt: 

GPT2TokenizerFast(name_or_path='skt/kogpt2-base-v2', vocab_size=51200, model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'bos_token': '<|endoftext|>', 'eos_token': '<|endoftext|>', 'unk_token': '<|endoftext|>'}, clean_up_tokenization_spaces=True)

In [11]:
# 데이터 로드
data = pd.read_csv(cfg.train_data_path)

# 토크나이저 로드
tokenizer = AutoTokenizer.from_pretrained('skt/kogpt2-base-v2')


# 데이터 포맷팅 및 토크나이징
formatted_data = []
for _, row in tqdm(data.iterrows()):
    for q_col in ['질문_1', '질문_2']:
        for a_col in ['답변_1', '답변_2', '답변_3', '답변_4', '답변_5']:
            # 질문과 답변 쌍을 </s> token으로 연결
            input_text = row['category']+';'+row[q_col] + tokenizer.eos_token + row[a_col]
            print(input_text)
            input_ids = tokenizer.encode(input_text, return_tensors='pt')
            formatted_data.append(input_ids)
print('Done.')

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
138it [00:00, 683.17it/s]

건축구조;면진장치가 뭐야?<|endoftext|>면진장치란 지반에서 오는 진동 에너지를 흡수하여 건물에 주는 진동을 줄여주는 진동 격리장치입니다.
건축구조;면진장치가 뭐야?<|endoftext|>면진장치란 건물의 지반에서 발생하는 진동 에너지를 흡수하여 건물을 보호하고, 진동을 줄여주는 장치입니다. 주로 지진이나 기타 지반의 진동으로 인한 피해를 방지하기 위해 사용됩니다.
건축구조;면진장치가 뭐야?<|endoftext|>면진장치란 지반으로부터 발생하는 진동 에너지를 흡수하여 건물에 전달되는 진동을 줄여주는 장치를 말합니다. 이를 통해 건물의 안전성과 안정성을 향상시키고, 지진 등의 외부 충격으로부터 보호하는 역할을 합니다. 지진으로 인한 건물의 피해를 최소화하기 위해 주로 사용됩니다.
건축구조;면진장치가 뭐야?<|endoftext|>면진장치는 건물의 지반으로부터 오는 진동 에너지를 흡수하여 건물에 전달되는 진동을 최소화해 주는 진동 격리장치입니다. 이를 통해 건물 내부의 진동을 줄이고 안정성을 유지하는 데 도움을 줍니다.
건축구조;면진장치가 뭐야?<|endoftext|>면진장치는 건물에 오는 지반 진동의 영향을 최대한으로 흡수하여 건물에 전달되는 진동을 줄여주는 장치입니다. 지반으로부터 오는 진동 에너지의 영향을 완화시키기 위해 사용됩니다.
건축구조;면진장치에 사용되는 주요 기술은 무엇인가요?<|endoftext|>면진장치란 지반에서 오는 진동 에너지를 흡수하여 건물에 주는 진동을 줄여주는 진동 격리장치입니다.
건축구조;면진장치에 사용되는 주요 기술은 무엇인가요?<|endoftext|>면진장치란 건물의 지반에서 발생하는 진동 에너지를 흡수하여 건물을 보호하고, 진동을 줄여주는 장치입니다. 주로 지진이나 기타 지반의 진동으로 인한 피해를 방지하기 위해 사용됩니다.
건축구조;면진장치에 사용되는 주요 기술은 무엇인가요?<|endoftext|>면진장치란 지반으로부터 발생하는 진동 에너지를 흡수하여 건물에 전달되는 진동을 줄여주는 장치를 말합니다. 이를 통해 건물의 안

210it [00:00, 699.89it/s]

마감재;비드법 보온판 2종의 장점이 뭐야?<|endoftext|>비드법 보온판 2종은 단열성이 높고 시간이 지날수록 경시현상이 없고 습기, 곰팡이로부터 영향을 받지 않는다는 장점이 있습니다.
마감재;비드법 보온판 2종의 장점이 뭐야?<|endoftext|>비드법 보온판 2종은 단열성이 높아서 온도와 습도에 민감한 장소에서 사용하기에 적합합니다. 또한, 시간이 지날수록 경시현상이 발생하지 않고, 습기와 곰팡이로부터 영향을 받지 않는 점이 있어서 내구성이 좋다는 장점이 있습니다.
마감재;비드법 보온판 2종의 장점이 뭐야?<|endoftext|>비드법 보온판 2종은 단열성이 뛰어나며, 시간이 지나도 경시현상이 발생하지 않는 점이 있습니다. 또한, 습기와 곰팡이에 영향을 받지 않아서 내구성이 우수하다는 장점이 있습니다.
마감재;비드법 보온판 2종의 장점이 뭐야?<|endoftext|>비드법 보온판 2종은 단열성이 뛰어나 시간이 지나도 경시 현상이 없으며, 습기와 곰팡이에도 영향을 받지 않는 점이 주요 장점입니다. 이로써 건축물의 온도와 습도 조절에 뛰어난 효과를 발휘할 수 있습니다.
마감재;비드법 보온판 2종의 장점이 뭐야?<|endoftext|>비드법 보온판 2종은 단열성이 높을 뿐만 아니라 시간이 흐를수록 경시 현상이 없고, 습기와 곰팡이로부터 영향을 받지 않는 특징이 있습니다. 또한, 내구성이 뛰어나고 저밀도인 것도 높은 절연 효과를 보장하는데 도움이 됩니다.
마감재;비드법 보온판 2종을 사용하는 것의 장점은 무엇인가요?<|endoftext|>비드법 보온판 2종은 단열성이 높고 시간이 지날수록 경시현상이 없고 습기, 곰팡이로부터 영향을 받지 않는다는 장점이 있습니다.
마감재;비드법 보온판 2종을 사용하는 것의 장점은 무엇인가요?<|endoftext|>비드법 보온판 2종은 단열성이 높아서 온도와 습도에 민감한 장소에서 사용하기에 적합합니다. 또한, 시간이 지날수록 경시현상이 발생하지 않고, 습기와 곰팡이로부터 영향을 받지 않는 점이 있어서 내구성이 좋다는 장점이 

352it [00:00, 638.17it/s]

...

시공;내단열 시공을 하는 것의 장점은 무엇인가요?<|endoftext|>내단열 시공의 장점은 공사를 진행하는 동안 날씨의 영향을 덜 받을 뿐만 아니라 공사비, 재료비, 인건비가 적게 들어가는 것뿐만 아니라 외부벽체와 직접 닿지 않아 열교를 줄일 수 있다는 점입니다. 또한, 내단열을 통해 내부 온도를 안정적으로 유지할 수 있는데, 이는 에너지비 절감과 더불어 편안한 실내 환경을 제공한다는 장점으로도 작용합니다.
시공;내단열 시공을 하는 것의 장점은 무엇인가요?<|endoftext|>내단열 시공의 장점은 실내에서의 작업으로 인해 날씨의 영향을 덜 받는다는 것입니다. 또한 공사비, 재료비, 그리고 인건비가 적게 들어가며 외부 벽체와 직접 닿지 않기 때문에 열교 현상을 줄일 수 있다는 점도 있습니다. 이러한 이유들로 내단열 시공은 매우 경제적이고 효율적인 방법이라 할 수 있습니다.
시공;배관공사할 때 주의해야 할 점이 뭐야?<|endoftext|>배관공사 할 때 주의할 점은 기울기, 통기구 설치, 소제구 설치입니다.
시공;배관공사할 때 주의해야 할 점이 뭐야?<|endoftext|>배관공사를 할 때 주의해야 하는 점은 여러 가지가 있지만, 특히 중요한 사항은 다음과 같습니다: 1. 기울기: 배수 배관은 적절한 기울기를 가져야 합니다. 충분한 기울기가 없을 경우 배수가 원활하지 않아 배관이 막힐 수 있습니다. 2. 통기구 설치: 환기 및 냄새 제거를 위해 적절한 위치에 통기구를 설치해야 합니다. 부적절한 통기구 설치로 인해 고압력이나 공기 포집이 발생할 수 있습니다. 3. 소제구 설치: 소화수 공급을 위한 소제구는 적절한 위치와 안전한 시설 설치가 필요합니다. 소화수의 안정적인 공급을 위해 소제구 설치를 꼼꼼히 해야 합니다.
시공;배관공사할 때 주의해야 할 점이 뭐야?<|endoftext|>배관공사를 할 때 주의해야 할 점은 여러 가지가 있지만, 특히 기울기, 통기구 설치, 그리고 소제구 설치에 주의해야 합니다. 먼저, 배관은 올바른 기울기로 설치되어야 합니다. 왜냐하

611it [00:00, 586.53it/s]

인테리어;유럽의 클래식한 디자인을 집 내부에 반영하는 데 어떤 포인트를 주의해야 할까요?<|endoftext|>유럽 클래식한 디자인을 집 내부에 반영하기 위해서는 아키텍처 디테일과 대리석 가구와 같은 클래식한 소품들을 선택하는 것이 좋습니다. 또한, 서스펜션 조명을 활용하여 분위기 있는 조명을 조합할 수 있습니다. 그 외에도 고급스러운 커튼, 고전적인 패턴의 타일, 벽지, 그림 등을 활용하여 유럽의 클래식한 분위기를 살려낼 수 있습니다. 이를 통해 집 내부에서도 유럽의 역사적이고 우아한 느낌을 느낄 수 있을 것입니다.
인테리어;유럽의 클래식한 디자인을 집 내부에 반영하는 데 어떤 포인트를 주의해야 할까요?<|endoftext|>유럽 클래식한 디자인을 집 내부에 반영하려면 아키텍처 디테일과 대리석 가구, 그리고 서스펜션 조명을 선택하는 것이 좋습니다. 또한, 유럽의 클래식한 디자인을 표현하기 위해 화려한 칠러와 커튼, 고급스러운 카펫, 그리고 전통적인 패턴이 적용된 장식품 등을 활용할 수 있습니다.  특히, 유럽 클래식한 디자인에 특히 중요한 부분은 세부적인 디테일에 있습니다. 디테일한 테두리 디자인의 거울, 곡선이 돋보이는 가구 등을 활용하여 전통적이면서도 우아한 분위기를 연출할 수 있습니다. 또한, 조각상, 고전적인 그림, 그리고 돋보이는 벽지나 타일 디자인 등을 통해 집 내부에 유럽 클래식한 분위기를 조성할 수 있습니다.
인테리어;유럽의 클래식한 디자인을 집 내부에 반영하는 데 어떤 포인트를 주의해야 할까요?<|endoftext|>유럽 클래식한 디자인을 집 내부에 반영하려면 몇 가지 주의해야 할 점이 있습니다. 먼저, 디테일을 중요시하는 유럽 클래식한 스타일을 채택하는 것이 중요합니다. 대리석 가구와 같은 고급스러운 소재와 장식품을 사용하고, 서스펜션 조명을 선택하여 전통적이면서도 우아한 분위기를 연출할 수 있습니다. 또한, 정교한 아키텍처 디테일을 강조하여 집 내부에 유럽 클래식한 분위기를 조성할 수 있습니다. 따라서 건축 및 가구 디자인에 신중한 선택이

644it [00:01, 625.24it/s]

타 마감하자;벽장 부위 결로의 원인이 뭐야?<|endoftext|>벽장 부위 결로의 원인은 주로 난방이 자리잡은 방이 내부 온도가 낮은 반면, 외부 환기가 충분히 이뤄지지 않아 습도가 제대로 감소하지 못함으로써 발생합니다. 이때 난방이 인접한 방과 같은 조건을 가지고 있다면, 벽장 부위 결로가 나타날 수 있습니다.
타 마감하자;벽장 부위 결로의 원인이 뭐야?<|endoftext|>벽장 부위 결로가 발생하는 원인은 난방이 잘 이루어지지 않아 해당 공간이 저온인 반면, 환기가 충분히 이루어지지 않아 습도가 충분히 감소하지 못하는 경우입니다. 이로써 습도가 높아지고, 벽장 부위에서 결로가 발생하게 됩니다.
타 마감하자;벽장 부위 결로의 원인이 뭐야?<|endoftext|>벽장 부위 결로가 발생하는 원인은 난방이 인접한 방과 같은 조건을 갖추고 있지만, 환기가 충분히 이루어지지 않아 습도를 제거할 수 없는 상황에서 발생합니다. 결로는 주로 습기가 있는 환경에서 증발되는 수분이 벽면에 응축되어 생기는 것으로, 낮은 온도와 부족한 환기 때문에 발생할 수 있습니다. 즉, 합리적인 조건에서의 적절한 환기와 습도 관리가 필요한데, 벽장 부위 결로의 원인 중 습도와 환기의 관리가 중요한 역할을 합니다.
타 마감하자;벽장 부위 결로의 원인이 뭐야?<|endoftext|>벽장 부위 결로의 주된 원인은 충분한 환기가 이루어지지 않는 환경과 과도한 습기가 유입되는 것입니다. 특히 난방이 이웃한 방과 동일한 조건이 되나 그 방에 비해 저온인 상황에서 환기가 충분히 이루어지지 않을 경우에 결로가 발생할 수 있습니다. 따라서, 충분한 환기와 습도 관리가 필요하며, 추가적으로 절연재나 방수재를 사용하여 습기의 접근을 통제하는 것이 도움이 됩니다.
타 마감하자;벽장 부위 결로가 발생하는 주된 원인은 무엇일까요?<|endoftext|>벽장 부위 결로의 원인은 난방이 이웃한 방과동일한 조건이 되나 그 방에 비해 저온인 반면 환기가 실외로 되지 않아 습도감소가 불가능할 경우 발생합니다.
타 마감하자

In [10]:
formatted_data

[tensor([[ 9411,  8265, 37765, 46651,  7991,   406,     1,  9411,  8265, 20725,
           7374,  9027,  7599,  9023, 14472, 15898, 14820, 33220, 36928, 10764,
           9166, 11818, 28037, 10090, 15898, 34062, 20725, 21154]]),
 tensor([[ 9411,  8265, 37765, 46651,  7991,   406,     1,  9411,  8265, 20725,
           7374, 16759,  9027,  7599,  9023, 13426, 15898, 14820, 33220, 17836,
          10146,  9307,  9166, 11818, 28037, 10090, 16668, 21154,  9584, 15351,
           9185, 10493,  9027, 16652,  9166, 12999, 11931, 14581, 22489,  9207,
           9209,  7255, 12521]]),
 tensor([[ 9411,  8265, 37765, 46651,  7991,   406,     1,  9411,  8265, 20725,
           7374,  9027,  7599, 10306, 13426, 15898, 14820, 33220, 36928, 43591,
           9166, 11818, 28037, 10090, 21547,  9135, 37194,  9558,  9430, 16759,
          11350, 10342, 44444, 15072, 15877, 15351,  9284, 13387, 21827, 10306,
          23227, 10254, 49421, 15351,  9021, 11931, 16759, 14581, 17031, 24092,
           9207, 

## Model Fine-tuning

In [12]:
model = GPT2LMHeadModel.from_pretrained('skt/kogpt2-base-v2')
model.to(device) # 모델을

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(51200, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
      (1): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dro

In [10]:
model.parameters

<bound method Module.parameters of GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(51200, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
      (1): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=Fa

In [13]:
# 모델 로드
model = GPT2LMHeadModel.from_pretrained('skt/kogpt2-base-v2')
model.to(device) # 모델을 GPU단으로 이동

# 모델 학습 하이퍼파라미터(Hyperparameter) 세팅
# 실제 필요에 따라 조정하세요.
CFG = {
    'LR' : 3e-4, # Learning Rate
    'EPOCHS' : 20, # 학습 Epoch
}

# 모델 학습 설정
optimizer = AdamW(model.parameters(), lr=CFG['LR'])
model.train()

# 모델 학습
for epoch in range(CFG['EPOCHS']):
    total_loss = 0
    progress_bar = tqdm(enumerate(formatted_data), total=len(formatted_data))
    for batch_idx, batch in progress_bar:
        # 데이터를 GPU단으로 이동
        batch = batch.to(device)
        outputs = model(batch, labels=batch)
        loss = outputs.loss
        loss.backward()
        optimizer.step()
        optimizer.zero_grad()

        total_loss += loss.item()

        # 진행률 표시줄에 평균 손실 업데이트
        progress_bar.set_description(f"Epoch {epoch+1} - Avg Loss: {total_loss / (batch_idx+1):.4f}")

    # 에폭의 평균 손실을 출력
    print(f"Epoch {epoch+1}/{CFG['EPOCHS']}, Average Loss: {total_loss / len(formatted_data)}")

# 모델 저장
model.save_pretrained("./hansoldeco-kogpt2")
tokenizer.save_pretrained("./hansoldeco-kogpt2")

c:\Users\user\anaconda3\envs\PY39_\lib\site-packages\transformers\optimization.py:391: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
  0%|          | 0/6440 [00:02<?, ?it/s]


RuntimeError: philox_cuda_state for an unexpected CUDA generator used during capture. In regions captured by CUDA graphs, you may only use the default CUDA RNG generator on the device that's current when capture begins. If you need a non-default (user-supplied) generator, or a generator on another device, please file an issue.

## Model Inference

In [6]:
# 저장된 Fine-tuned 모델과 토크나이저 불러오기
model_dir = "./hansoldeco-kogpt2"
model = GPT2LMHeadModel.from_pretrained(model_dir)
model.to(device)
tokenizer = PreTrainedTokenizerFast.from_pretrained(model_dir)

# Inference를 위한 test.csv 파일 로드
test = pd.read_csv('./test.csv')

# test.csv의 '질문'에 대한 '답변'을 저장할 리스트
preds = []

# '질문' 컬럼의 각 질문에 대해 답변 생성
for test_question in tqdm(test['질문']):
    # 입력 텍스트를 토큰화하고 모델 입력 형태로 변환
    input_ids = tokenizer.encode(test_question + tokenizer.eos_token, return_tensors='pt')

    # 답변 생성
    output_sequences = model.generate(
        input_ids=input_ids.to(device),
        max_length=300,
        temperature=0.9,
        top_k=1,
        top_p=0.9,
        repetition_penalty=1.2,
        do_sample=True,
        num_return_sequences=1
    )

    # 생성된 텍스트(답변) 저장
    for generated_sequence in output_sequences:
        full_text = tokenizer.decode(generated_sequence, skip_special_tokens=False)
        # 질문과 답변의 사이를 나타내는 eos_token (</s>)를 찾아, 이후부터 출력
        answer_start = full_text.find(tokenizer.eos_token) + len(tokenizer.eos_token)
        answer_only = full_text[answer_start:].strip()
        answer_only = answer_only.replace('\n', ' ')
        preds.append(answer_only)

100%|██████████| 130/130 [04:54<00:00,  2.26s/it]


## Submission

In [7]:
# Test 데이터셋의 모든 질의에 대한 답변으로부터 512 차원의 Embedding Vector 추출
# 평가를 위한 Embedding Vector 추출에 활용하는 모델은 'distiluse-base-multilingual-cased-v1' 이므로 반드시 확인해주세요.
from sentence_transformers import SentenceTransformer # SentenceTransformer Version 2.2.2

# Embedding Vector 추출에 활용할 모델(distiluse-base-multilingual-cased-v1) 불러오기
model = SentenceTransformer('distiluse-base-multilingual-cased-v1')

# 생성한 모든 응답(답변)으로부터 Embedding Vector 추출
pred_embeddings = model.encode(preds)
pred_embeddings.shape

(130, 512)

In [8]:
submit = pd.read_csv('./sample_submission.csv')
# 제출 양식 파일(sample_submission.csv)을 활용하여 Embedding Vector로 변환한 결과를 삽입
submit.iloc[:,1:] = pred_embeddings
submit.head()

id     vec_0     vec_1     vec_2     vec_3     vec_4     vec_5   
0  TEST_000  0.015765  0.056010 -0.011973  0.009514  0.125522  0.007938  \
1  TEST_001  0.027476  0.031406 -0.050489  0.009678  0.119823 -0.041251   
2  TEST_002 -0.006813 -0.003179  0.008923  0.005651  0.090779 -0.008267   
3  TEST_003  0.012931  0.017019  0.002525  0.036831  0.078396 -0.030940   
4  TEST_004  0.020637  0.020052 -0.005806 -0.010334  0.105124 -0.003586   

      vec_6     vec_7     vec_8  ...   vec_502   vec_503   vec_504   vec_505   
0  0.031350  0.061990  0.010081  ... -0.007705 -0.013325  0.000010 -0.005996  \
1  0.014243 -0.017895  0.081403  ... -0.033637 -0.013678 -0.026174 -0.019957   
2 -0.041220  0.001288  0.029889  ... -0.036412 -0.062878 -0.003894 -0.047650   
3 -0.059503  0.019713  0.016635  ... -0.031194 -0.006522  0.066188 -0.042110   
4  0.035843  0.059211 -0.016760  ...  0.009173 -0.035664  0.047057 -0.003688   

    vec_506   vec_507   vec_508   vec_509   vec_510   vec_511  
0 -0.020423  0.008186  0.062777  0.031447 -0.012665  0.036256  
1 -0.005777  0.023247  0.020694 -0.020786 -0.049734 -0.011270  
2  0.034637  0.044994 -0.026444 -0.049396 -0.024263  0.032262  
3  0.003480  0.019691 -0.018142 -0.016340 -0.028830  0.026559  
4  0.013008  0.012201  0.001192  0.012827  0.019431  0.038264  

[5 rows x 513 columns]

In [9]:
# 리더보드 제출을 위한 csv파일 생성
submit.to_csv('./baseline_submit.csv', index=False)